In [1]:
import ydf
import tensorflow as tf
import pandas as pd

2026-01-21 07:24:48.894250: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1768973088.987939   12675 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1768973089.014759   12675 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1768973089.226957   12675 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1768973089.226973   12675 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1768973089.226975   12675 computation_placer.cc:177] computation placer alr

In [2]:
ds_path = "https://raw.githubusercontent.com/google/yggdrasil-decision-forests/main/yggdrasil_decision_forests/test_data/dataset"

# Download and load the dataset into Pandas DataFrames
train_ds = pd.read_csv(f"{ds_path}/adult_train.csv")
test_ds = pd.read_csv(f"{ds_path}/adult_test.csv")

# Display the first 5 rows of the training data
train_ds.head(5)

age     workclass  fnlwgt     education  education_num      marital_status  \
0   44       Private  228057       7th-8th              4  Married-civ-spouse   
1   20       Private  299047  Some-college             10       Never-married   
2   40       Private  342164       HS-grad              9           Separated   
3   30       Private  361742  Some-college             10  Married-civ-spouse   
4   67  Self-emp-inc  171564       HS-grad              9  Married-civ-spouse   

          occupation   relationship   race     sex  capital_gain  \
0  Machine-op-inspct           Wife  White  Female             0   
1      Other-service  Not-in-family  White  Female             0   
2       Adm-clerical      Unmarried  White  Female             0   
3    Exec-managerial        Husband  White    Male             0   
4     Prof-specialty           Wife  White  Female         20051   

   capital_loss  hours_per_week      native_country income  
0             0              40  Dominican-Republic  <=50K  
1             0              20       United-States  <=50K  
2             0              37       United-States  <=50K  
3             0              50       United-States  <=50K  
4             0              30             England   >50K

In [3]:
model = ydf.GradientBoostedTreesLearner(label="income").train(train_ds)

Train model on 22792 examples
Model trained in 0:00:00.855874


In [4]:
model.describe()

## Model Tuning
**Model tuning**, also known as automated model hyperparameter optimization or AutoML, involves finding the optimal hyperparameters for a learner to maximize the performance of a model. YDF supports model tuning out-of-the-box.

In [5]:
# Download a classification dataset and load it as a Pandas DataFrame.
ds_path = "https://raw.githubusercontent.com/google/yggdrasil-decision-forests/main/yggdrasil_decision_forests/test_data/dataset"
train_ds = pd.read_csv(f"{ds_path}/adult_train.csv")
test_ds = pd.read_csv(f"{ds_path}/adult_test.csv")

# Print the first 5 training examples
train_ds.head(5)

age     workclass  fnlwgt     education  education_num      marital_status  \
0   44       Private  228057       7th-8th              4  Married-civ-spouse   
1   20       Private  299047  Some-college             10       Never-married   
2   40       Private  342164       HS-grad              9           Separated   
3   30       Private  361742  Some-college             10  Married-civ-spouse   
4   67  Self-emp-inc  171564       HS-grad              9  Married-civ-spouse   

          occupation   relationship   race     sex  capital_gain  \
0  Machine-op-inspct           Wife  White  Female             0   
1      Other-service  Not-in-family  White  Female             0   
2       Adm-clerical      Unmarried  White  Female             0   
3    Exec-managerial        Husband  White    Male             0   
4     Prof-specialty           Wife  White  Female         20051   

   capital_loss  hours_per_week      native_country income  
0             0              40  Dominican-Republic  <=50K  
1             0              20       United-States  <=50K  
2             0              37       United-States  <=50K  
3             0              50       United-States  <=50K  
4             0              30             England   >50K

In [6]:
tuner = ydf.RandomSearchTuner(num_trials=50)
tuner.choice("shrinkage", [0.2, 0.1, 0.05])
tuner.choice("subsample", [1.0, 0.9, 0.8])
tuner.choice("max_depth", [3, 4, 5, 6])

In [7]:
learner = ydf.GradientBoostedTreesLearner(
    label="income",
    num_trees=100, # Used for all the trials.
    tuner=tuner,
)
model = learner.train(train_ds)

Train model on 22792 examples
Model trained in 0:00:11.089650


In [8]:
model.describe()

In [10]:
model.evaluate(test_ds)

Evaluation()

### Local tuning with automatically configured hyper-parameters
If you do not want to configure the hyperparameters to optimize, you can use a preconfigured tuner.

In [11]:
tuner = ydf.RandomSearchTuner(num_trials=50, automatic_search_space=True)

In [12]:
learner = ydf.GradientBoostedTreesLearner(
    label="income",
    num_trees=100,
    tuner=tuner,
)
model =learner.train(train_ds)

Train model on 22792 examples
Model trained in 0:04:16.386563


In [15]:
model.evaluate(test_ds)

Evaluation()

In [16]:
ydf.RandomSearchTuner?

Init signature:
ydf.RandomSearchTuner(
    num_trials: int = 100,
    automatic_search_space: bool = False,
    parallel_trials: int = 1,
    max_trial_duration: Optional[float] = None,
    *,
    cross_validation: bool = False,
    cross_validation_num_folds: Optional[int] = None,
)
Docstring:     
Tuner using random search.

The candidate hyper-parameter can be evaluated independently and in parallel.

Attributes:
  num_trials: Number of hyperparameter configurations to evaluate.
  automatic_search_space: If true, automatically define the search space of
    hyperparameters. In this case, configuring the hyperparameters manually
    (e.g. calling "choice(...)" on the tuner) is not necessary.
  parallel_trials: Number of trials to evaluate in parallel. The training of
    an individual model uses "num_threads" threads (configured in the
    learner). Therefore, in the non-distributed training setting, the total
    number of threads will be `parallel_trials x num_threads`. In the
    